In [ ]:
#prophet

In [1]:
!pip install prophet

Defaulting to user installation because normal site-packages is not writeable


In [2]:
import pandas as pd
import os
from prophet import Prophet
import joblib
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import numpy as np
import matplotlib.pyplot as plt

# -----------------------------
# Paths
# -----------------------------
input_folder = "dataset"
output_models = "prophet_output_models"
output_csv = "prophet_output_csv"
output_graphs = "prophet_output_graphs"
output_metrics_csv = "prophet_metrics.csv"

os.makedirs(output_models, exist_ok=True)
os.makedirs(output_csv, exist_ok=True)
os.makedirs(output_graphs, exist_ok=True)

# -----------------------------
# Prepare metrics storage
# -----------------------------
metrics_list = []

# -----------------------------
# Function to handle multiple date formats
# -----------------------------
def parse_dates(date_series):
    """Try multiple date formats and return parsed dates"""
    for fmt in ("%Y-%m-%d", "%d-%m-%Y", "%d/%m/%Y", "%m/%d/%Y"):
        try:
            return pd.to_datetime(date_series, format=fmt, errors="coerce")
        except:
            continue
    # fallback: let pandas auto-infer
    return pd.to_datetime(date_series, errors="coerce")

# -----------------------------
# Process each CSV
# -----------------------------
for file in os.listdir(input_folder):
    if file.endswith(".csv"):
        file_path = os.path.join(input_folder, file)
        print(f"\n========== Processing: {file} ==========")

        # Load CSV
        df = pd.read_csv(file_path)

        # Parse dates
        df['Date'] = parse_dates(df['Date'])
        if df['Date'].isna().sum() > 0:
            print(f"⚠️ Warning: {df['Date'].isna().sum()} invalid dates found and dropped")
            df = df.dropna(subset=['Date'])

        df = df.sort_values('Date')

        # Handle missing values
        if df['Average Price'].isna().sum() > 0:
            mean_value = df['Average Price'].mean()
            df['Average Price'] = df['Average Price'].fillna(mean_value)
            print(f"Filled missing values with mean: {mean_value:.2f}")

        # Prepare data for Prophet
        prophet_df = df[['Date', 'Average Price']].rename(columns={'Date': 'ds', 'Average Price': 'y'})

        # Build and fit Prophet model
        model = Prophet(daily_seasonality=True)
        model.fit(prophet_df)

        # Predict for existing dates
        future = model.make_future_dataframe(periods=0)
        forecast = model.predict(future)
        df['Predicted'] = forecast['yhat'].values

        # Round Actual and Predicted to 2 decimals
        df['Average Price'] = df['Average Price'].round(2)
        df['Predicted'] = df['Predicted'].round(2)

        # Save CSV with Actual vs Predicted
        output_df = df[['Date', 'Average Price', 'Predicted']].rename(columns={'Average Price': 'Actual'})
        updated_csv_path = os.path.join(output_csv, file.replace(".csv", "_prophet_results.csv"))
        output_df.to_csv(updated_csv_path, index=False)

        # Calculate metrics
        y_true = df['Average Price'].values
        y_pred = df['Predicted'].values

        mae = round(mean_absolute_error(y_true, y_pred), 2)
        rmse = round(np.sqrt(mean_squared_error(y_true, y_pred)), 2)
        r2 = round(r2_score(y_true, y_pred), 2)
        mape = round(np.mean(np.abs((y_true - y_pred) / y_true)) * 100, 2)
        accuracy = round(100 - mape, 2)

        # Print metrics
        print(f"Metrics for {file}:")
        print(f"  MAE      : {mae}")
        print(f"  RMSE     : {rmse}")
        print(f"  R²       : {r2}")
        print(f"  MAPE     : {mape}%")
        print(f"  Accuracy : {accuracy}%")

        # Save metrics
        metrics_list.append({
            'File': file,
            'MAE': mae,
            'RMSE': rmse,
            'R2': r2,
            'MAPE(%)': mape,
            'Accuracy(%)': accuracy
        })

        # Save model
        model_file = os.path.join(output_models, file.replace(".csv", "_prophet_model.pkl"))
        joblib.dump(model, model_file)

        # Save Graph
        plt.figure(figsize=(10, 6))
        plt.plot(df['Date'], df['Average Price'], label='Actual', color='blue', linewidth=2)
        plt.plot(df['Date'], df['Predicted'], label='Predicted', color='red', linewidth=2, linestyle='--')
        plt.title(f"Actual vs Predicted - {file}", fontsize=14)
        plt.xlabel("Date", fontsize=12)
        plt.ylabel("Price", fontsize=12)
        plt.legend()
        plt.grid(True, alpha=0.3)
        plt.tight_layout()

        graph_path = os.path.join(output_graphs, file.replace(".csv", "_prophet_graph.png"))
        plt.savefig(graph_path)
        plt.close()

# Save all metrics to CSV
metrics_df = pd.DataFrame(metrics_list)
metrics_df.to_csv(output_metrics_csv, index=False)
print(f"\n✅ All districts processed! Metrics saved to {output_metrics_csv}, CSV results saved, and graphs generated.")


========== Processing: wheat_Bagalkot_weekly.csv ==========


19:58:16 - cmdstanpy - INFO - Chain [1] start processing
19:58:17 - cmdstanpy - INFO - Chain [1] done processing


Metrics for wheat_Bagalkot_weekly.csv:
  MAE      : 166.96
  RMSE     : 280.34
  R²       : 0.69
  MAPE     : 7.4%
  Accuracy : 92.6%


19:58:18 - cmdstanpy - INFO - Chain [1] start processing



========== Processing: wheat_Bangalore_weekly.csv ==========


...

Metrics for wheat_Raichur_weekly.csv:
  MAE      : 86.24
  RMSE     : 110.22
  R²       : 0.91
  MAPE     : 4.95%
  Accuracy : 95.05%

========== Processing: wheat_Shimoga_weekly.csv ==========


19:58:43 - cmdstanpy - INFO - Chain [1] start processing
19:58:43 - cmdstanpy - INFO - Chain [1] done processing


Metrics for wheat_Shimoga_weekly.csv:
  MAE      : 140.03
  RMSE     : 266.96
  R²       : 0.73
  MAPE     : 5.54%
  Accuracy : 94.46%

========== Processing: wheat_Tumkur_weekly.csv ==========


19:58:44 - cmdstanpy - INFO - Chain [1] start processing
19:58:44 - cmdstanpy - INFO - Chain [1] done processing


Metrics for wheat_Tumkur_weekly.csv:
  MAE      : 240.12
  RMSE     : 505.49
  R²       : 0.59
  MAPE     : 8.56%
  Accuracy : 91.44%

✅ All districts processed! Metrics saved to prophet_metrics.csv, CSV results saved, and graphs generated.


In [ ]:
#ARIMA

In [3]:
import pandas as pd
import numpy as np
import os
import matplotlib.pyplot as plt
from statsmodels.tsa.arima.model import ARIMA
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import joblib
import warnings
warnings.filterwarnings("ignore")

# -----------------------------
# Create output directories
# -----------------------------
input_folder = "dataset"
output_models = "arima_output_models"
output_csv = "arima_output_csv"
output_graphs = "arima_output_graphs"
output_logs = "arima_output_logs"
output_metrics = "arima_output_metrics"

os.makedirs(output_models, exist_ok=True)
os.makedirs(output_csv, exist_ok=True)
os.makedirs(output_graphs, exist_ok=True)
os.makedirs(output_logs, exist_ok=True)
os.makedirs(output_metrics, exist_ok=True)

# Metrics collector
all_metrics = []

# -----------------------------
# Helper function for flexible date parsing
# -----------------------------
def parse_dates(date_series):
    """Try multiple date formats until successful."""
    for fmt in ("%Y-%m-%d", "%d-%m-%Y", "%d/%m/%Y", "%Y/%m/%d"):
        try:
            return pd.to_datetime(date_series, format=fmt)
        except Exception:
            continue
    return pd.to_datetime(date_series, errors="coerce")  # fallback

# -----------------------------
# Process each CSV file
# -----------------------------
for file in os.listdir(input_folder):
    if file.endswith(".csv"):
        file_path = os.path.join(input_folder, file)
        print(f"Processing: {file}")

        try:
            # Load CSV
            df = pd.read_csv(file_path)

            # Handle multiple date formats
            df['Date'] = parse_dates(df['Date'])
            df = df.dropna(subset=['Date'])
            df = df.sort_values('Date')
            df.set_index('Date', inplace=True)

            # Handle NaN values in Average Price
            df['Average Price'] = df['Average Price'].fillna(df['Average Price'].mean())

            # Add moving averages
            df['MA_7'] = df['Average Price'].rolling(window=7).mean()
            df['MA_30'] = df['Average Price'].rolling(window=30).mean()

            # ARIMA parameters (static, can be tuned later)
            p, d, q = 5, 1, 0
            model = ARIMA(df['Average Price'], order=(p, d, q))
            model_fit = model.fit()

            # Save ARIMA model
            model_file = os.path.join(output_models, file.replace(".csv", "_arima_model.pkl"))
            joblib.dump(model_fit, model_file)

            # Predictions
            predictions = model_fit.predict(start=0, end=len(df)-1, typ='levels')
            df['Predicted'] = predictions

            # Round Actual and Predicted to 2 decimals
            df['Average Price'] = df['Average Price'].round(2)
            df['Predicted'] = df['Predicted'].round(2)

            # Save Actual vs Predicted CSV
            comparison_df = pd.DataFrame({
                "Date": df.index,
                "Actual": df['Average Price'],
                "Predicted": df['Predicted']
            })
            comparison_csv = os.path.join(output_csv, file.replace(".csv", "_arima_actual_vs_predicted.csv"))
            comparison_df.to_csv(comparison_csv, index=False)

            # Calculate metrics
            mae = round(mean_absolute_error(df['Average Price'], df['Predicted']), 2)
            rmse = round(np.sqrt(mean_squared_error(df['Average Price'], df['Predicted'])), 2)
            r2 = round(r2_score(df['Average Price'], df['Predicted']), 2)
            mape = round(np.mean(np.abs((df['Average Price'] - df['Predicted']) / df['Average Price'])) * 100, 2)
            accuracy = round(100 - mape, 2)

            all_metrics.append({
                "District": file.replace(".csv", ""),
                "MAE": mae,
                "RMSE": rmse,
                "R2": r2,
                "MAPE(%)": mape,
                "Accuracy (%)": accuracy
            })

            # Print metrics
            print(f"Metrics for {file}:")
            print(f"  MAE      : {mae}")
            print(f"  RMSE     : {rmse}")
            print(f"  R²       : {r2}")
            print(f"  MAPE     : {mape}%")
            print(f"  Accuracy : {accuracy}%\n")

            # Save graph
            plt.figure(figsize=(12,6))
            plt.plot(df.index, df['Average Price'], label="Actual", color="blue", linewidth=2)
            plt.plot(df.index, df['Predicted'], label="Predicted (ARIMA)", color="red", linestyle="dashed", linewidth=2)
            plt.plot(df.index, df['MA_7'], label="MA 7", color="orange")
            plt.plot(df.index, df['MA_30'], label="MA 30", color="green")
            plt.xlabel("Date")
            plt.ylabel("Average Price")
            plt.title(f"Price Prediction (ARIMA) - {file}")
            plt.legend()
            plt.grid(True)
            graph_file = os.path.join(output_graphs, file.replace(".csv", "_arima_graph.png"))
            plt.savefig(graph_file)
            plt.close()

            # Save logs
            log_file = os.path.join(output_logs, file.replace(".csv", "_arima_training.txt"))
            with open(log_file, "w", encoding="utf-8") as f:
                f.write(f"ARIMA model fitted for {file}.\n")
                f.write(f"ARIMA Order: (p={p}, d={d}, q={q})\n")
                f.write(f"MAE: {mae}, RMSE: {rmse}, R²: {r2}, MAPE: {mape}%, Accuracy: {accuracy}%\n")
                f.write("Predictions, Graph, Logs saved.\n")

            print(f"Done with {file} | Model, CSV, Graph, Metrics, Log saved.\n")

        except Exception as e:
            print(f"Error processing {file}: {e}")

# -----------------------------
# Save all metrics in one CSV
# -----------------------------
if all_metrics:
    metrics_df = pd.DataFrame(all_metrics)
    metrics_csv = os.path.join(output_metrics, "arima_all_districts_metrics.csv")
    metrics_df.to_csv(metrics_csv, index=False)
    print(f"All metrics saved to {metrics_csv}")

Processing: wheat_Bagalkot_weekly.csv
Metrics for wheat_Bagalkot_weekly.csv:
  MAE      : 35.67
  RMSE     : 94.85
  R²       : 0.96
  MAPE     : 1.73%
  Accuracy : 98.27%

Done with wheat_Bagalkot_weekly.csv | Model, CSV, Graph, Metrics, Log saved.

Processing: wheat_Bangalore_weekly.csv
Metrics for wheat_Bangalore_weekly.csv:
  MAE      : 41.93
  RMSE     : 136.98
  R²       : 0.94
  MAPE     : 1.73%
  Accuracy : 98.27%

Done with wheat_Bangalore_weekly.csv | Model, CSV, Graph, Metrics, Log saved.

Processing: wheat_Belgaum_weekly.csv
Metrics for wheat_Belgaum_weekly.csv:
  MAE      : 27.21
  RMSE     : 69.34
  R²       : 0.98
  MAPE     : 1.35%
  Accuracy : 98.65%

Done with wheat_Belgaum_weekly.csv | Model, CSV, Graph, Metrics, Log saved.

Processing: wheat_Bellary_weekly.csv
Metrics for wheat_Bellary_weekly.csv:
  MAE      : 24.14
  RMSE     : 73.9
  R²       : 0.99
  MAPE     : 1.34%
  Accuracy : 98.66%

Done with wheat_Bellary_weekly.csv | Model, CSV, Graph, Metrics, Log saved.


In [ ]:
#SARIMAX

In [4]:
import pandas as pd
import numpy as np
import os
import matplotlib.pyplot as plt
from statsmodels.tsa.statespace.sarimax import SARIMAX
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import warnings
import joblib

warnings.filterwarnings("ignore")  # Ignore warnings

# -----------------------------
# Paths
# -----------------------------
input_folder = "dataset"
output_models = "sarimax_output_models"
output_csv = "sarimax_output_csv"
output_graphs = "sarimax_output_graphs"
output_metrics_csv = "sarimax_metrics.csv"

os.makedirs(output_models, exist_ok=True)
os.makedirs(output_csv, exist_ok=True)
os.makedirs(output_graphs, exist_ok=True)

# -----------------------------
# Metrics storage
# -----------------------------
metrics_list = []

# -----------------------------
# Process each CSV
# -----------------------------
for file in os.listdir(input_folder):
    if file.endswith(".csv"):
        file_path = os.path.join(input_folder, file)
        print(f"========== Processing: {file} ==========")

        # Load CSV
        df = pd.read_csv(file_path)

        # Handle multiple date formats
        try:
            df['Date'] = pd.to_datetime(df['Date'], infer_datetime_format=True, errors='coerce')
        except Exception as e:
            print(f"Date conversion failed: {e}")
            continue

        df = df.dropna(subset=['Date'])  # Drop rows where date conversion failed
        df = df.sort_values('Date')
        df.set_index('Date', inplace=True)

        # Handle missing values
        if df['Average Price'].isna().sum() > 0:
            mean_value = df['Average Price'].mean()
            df['Average Price'].fillna(mean_value, inplace=True)
            print(f"Filled missing values with mean: {mean_value:.2f}")

        # Add moving averages
        df['MA_7'] = df['Average Price'].rolling(window=7).mean()
        df['MA_30'] = df['Average Price'].rolling(window=30).mean()

        # SARIMAX order (tune if needed)
        order = (1, 1, 1)
        seasonal_order = (1, 1, 1, 7)

        # Fit SARIMAX model
        model = SARIMAX(df['Average Price'],
                        order=order,
                        seasonal_order=seasonal_order,
                        enforce_stationarity=False,
                        enforce_invertibility=False)
        model_fit = model.fit(disp=False)

        # Save model
        model_file = os.path.join(output_models, file.replace(".csv", "_sarimax_model.pkl"))
        joblib.dump(model_fit, model_file)

        # Predictions
        df['Predicted'] = model_fit.predict(start=0, end=len(df)-1)

        # Round Actual and Predicted to 2 decimals
        df['Average Price'] = df['Average Price'].round(2)
        df['Predicted'] = df['Predicted'].round(2)

        # Calculate metrics
        y_true = df['Average Price'].values
        y_pred = df['Predicted'].values
        mae = round(mean_absolute_error(y_true, y_pred), 2)
        rmse = round(np.sqrt(mean_squared_error(y_true, y_pred)), 2)
        r2 = round(r2_score(y_true, y_pred), 2)
        mape = round(np.mean(np.abs((y_true - y_pred) / y_true)) * 100, 2)
        accuracy = round(100 - mape, 2)

        # Display metrics
        print(f"Metrics for {file}:")
        print(f"  MAE      : {mae}")
        print(f"  RMSE     : {rmse}")
        print(f"  R²       : {r2}")
        print(f"  MAPE     : {mape}%")
        print(f"  Accuracy : {accuracy}%\n")

        # Save metrics to list
        metrics_list.append({
            'File': file,
            'MAE': mae,
            'RMSE': rmse,
            'R2': r2,
            'MAPE(%)': mape,
            'Accuracy(%)': accuracy
        })

        # Save Actual vs Predicted CSV
        actual_vs_pred = df[['Average Price', 'Predicted']].reset_index()
        actual_vs_pred.rename(columns={'Average Price': 'Actual'}, inplace=True)
        updated_csv_path = os.path.join(output_csv, file.replace(".csv", "_sarimax_actual_vs_predicted.csv"))
        actual_vs_pred.to_csv(updated_csv_path, index=False)

        # Save graph
        plt.figure(figsize=(12,6))
        plt.plot(df.index, df['Average Price'], label="Actual", color="blue")
        plt.plot(df.index, df['MA_7'], label="MA 7", color="orange")
        plt.plot(df.index, df['MA_30'], label="MA 30", color="green")
        plt.plot(df.index, df['Predicted'], label="Predicted (SARIMAX)", color="red", linestyle="dashed")
        plt.xlabel("Date")
        plt.ylabel("Average Price")
        plt.title(f"Price Prediction (SARIMAX) - {file}")
        plt.legend()
        plt.grid(True)
        graph_file = os.path.join(output_graphs, file.replace(".csv", "_sarimax_graph.png"))
        plt.savefig(graph_file)
        plt.close()

# -----------------------------
# Save all metrics to CSV
# -----------------------------
metrics_df = pd.DataFrame(metrics_list)
metrics_df.to_csv(output_metrics_csv, index=False)

print(f"✅ All districts processed! Metrics saved to {output_metrics_csv}, predictions CSVs, graphs, and models generated.")

========== Processing: wheat_Bagalkot_weekly.csv ==========
Metrics for wheat_Bagalkot_weekly.csv:
  MAE      : 40.16
  RMSE     : 105.59
  R²       : 0.96
  MAPE     : 2.07%
  Accuracy : 97.93%

========== Processing: wheat_Bangalore_weekly.csv ==========
Metrics for wheat_Bangalore_weekly.csv:
  MAE      : 42.91
  RMSE     : 150.4
  R²       : 0.93
  MAPE     : 1.81%
  Accuracy : 98.19%

========== Processing: wheat_Belgaum_weekly.csv ==========
Metrics for wheat_Belgaum_weekly.csv:
  MAE      : 29.71
  RMSE     : 81.46
  R²       : 0.98
  MAPE     : 1.53%
  Accuracy : 98.47%

========== Processing: wheat_Bellary_weekly.csv ==========
Filled missing values with mean: 1829.87
Metrics for wheat_Bellary_weekly.csv:
  MAE      : 27.58
  RMSE     : 80.13
  R²       : 0.98
  MAPE     : 1.56%
  Accuracy : 98.44%

========== Processing: wheat_Bidar_weekly.csv ==========
Metrics for wheat_Bidar_weekly.csv:
  MAE      : 64.4
  RMSE     : 114.28
  R²       : 0.95
  MAPE     : 2.87%
  Accuracy :

In [ ]:
#TAT + MHA

In [5]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import tensorflow as tf
from tensorflow.keras import layers, models, optimizers

# -----------------------------
# Output directories
# -----------------------------
input_folder = "dataset"
output_models = "tat_output_models"
output_csv = "tat_output_csv"
output_graphs = "tat_output_graphs"
output_logs = "tat_output_logs"
metrics_file = "tat_metrics.csv"

os.makedirs(output_models, exist_ok=True)
os.makedirs(output_csv, exist_ok=True)
os.makedirs(output_graphs, exist_ok=True)
os.makedirs(output_logs, exist_ok=True)

# -----------------------------
# Function to create dataset
# -----------------------------
def create_dataset(data, look_back=30):
    X, y = [], []
    for i in range(len(data) - look_back):
        X.append(data[i:i+look_back, 0])
        y.append(data[i+look_back, 0])
    return np.array(X), np.array(y)

# -----------------------------
# Define Temporal Attention Transformer Model
# -----------------------------
def build_tat_model(input_shape, d_model=64, num_heads=4, ff_dim=128, dropout_rate=0.2):
    inputs = layers.Input(shape=input_shape)  # (look_back, 1)
    
    # Multi-Head Attention
    x = layers.MultiHeadAttention(num_heads=num_heads, key_dim=d_model)(inputs, inputs)
    x = layers.Dropout(dropout_rate)(x)
    x = layers.LayerNormalization(epsilon=1e-6)(x + inputs)  # Residual connection
    
    # Feed-Forward Network
    ff = layers.Dense(ff_dim, activation='relu')(x)
    ff = layers.Dense(input_shape[1])(ff)
    x = layers.LayerNormalization(epsilon=1e-6)(x + ff)  # Residual connection
    
    # Global Pooling
    x = layers.GlobalAveragePooling1D()(x)
    
    # Output
    outputs = layers.Dense(1)(x)
    
    model = models.Model(inputs=inputs, outputs=outputs)
    model.compile(optimizer=optimizers.Adam(learning_rate=0.001),
                  loss='mse', metrics=['mae'])
    return model

# -----------------------------
# Metrics storage
# -----------------------------
metrics_list = []

# -----------------------------
# Process each CSV file
# -----------------------------
look_back = 30
for file in os.listdir(input_folder):
    if file.endswith(".csv"):
        file_path = os.path.join(input_folder, file)
        print(f"🚀 Processing: {file}")

        # Load CSV
        df = pd.read_csv(file_path)
        
        # Handle multiple date formats
        try:
            df['Date'] = pd.to_datetime(df['Date'], infer_datetime_format=True, errors='coerce')
        except Exception as e:
            print(f"Date conversion failed: {e}")
            continue
        
        df = df.dropna(subset=['Date'])
        df = df.sort_values('Date')

        # Replace NaN in 'Average Price' with column mean
        df['Average Price'].fillna(df['Average Price'].mean(), inplace=True)

        # Add moving averages
        df['MA_7'] = df['Average Price'].rolling(window=7).mean()
        df['MA_30'] = df['Average Price'].rolling(window=30).mean()

        # Replace NaN in moving averages with column mean
        df['MA_7'].fillna(df['MA_7'].mean(), inplace=True)
        df['MA_30'].fillna(df['MA_30'].mean(), inplace=True)

        # Prepare data using MinMaxScaler
        values = df[['Average Price']].values.astype('float32')
        scaler = MinMaxScaler(feature_range=(0, 1))
        scaled_values = scaler.fit_transform(values)

        # Create sequences
        X, y = create_dataset(scaled_values, look_back)
        X = np.reshape(X, (X.shape[0], X.shape[1], 1))

        # Build model
        model = build_tat_model(input_shape=(look_back,1))
        model.summary()

        # Train model
        history = model.fit(X, y, epochs=100, batch_size=16, validation_split=0.2, verbose=1)

        # Save training logs
        log_file = os.path.join(output_logs, file.replace(".csv", "_tat_training.txt"))
        with open(log_file, "w") as f:
            f.write("Training Loss per Epoch:\n")
            for i, loss in enumerate(history.history['loss']):
                f.write(f"Epoch {i+1}: Loss={loss}, Val_Loss={history.history['val_loss'][i]}\n")

        # Predictions
        predictions = model.predict(X)
        predictions_rescaled = scaler.inverse_transform(predictions)
        df['Predicted'] = [np.nan]*look_back + list(predictions_rescaled.flatten())

        # Round Actual and Predicted to 2 decimals
        df['Average Price'] = df['Average Price'].round(2)
        df['Predicted'] = df['Predicted'].round(2)

        # Compute metrics
        y_true = df['Average Price'].values[look_back:]
        y_pred = predictions_rescaled.flatten()
        mae = round(mean_absolute_error(y_true, y_pred), 2)
        rmse = round(np.sqrt(mean_squared_error(y_true, y_pred)), 2)
        r2 = round(r2_score(y_true, y_pred), 2)
        mape = round(np.mean(np.abs((y_true - y_pred) / y_true)) * 100, 2)
        accuracy = round(100 - mape, 2)

        metrics_list.append([file.replace(".csv",""), mae, rmse, r2, mape, accuracy])

        # Save model
        model_file = os.path.join(output_models, file.replace(".csv", "_tat_model.h5"))
        model.save(model_file)

        # Save CSV
        updated_csv_path = os.path.join(output_csv, file.replace(".csv", "_tat_updated.csv"))
        df.to_csv(updated_csv_path, index=False)

        # Save graph
        plt.figure(figsize=(12,6))
        plt.plot(df['Date'], df['Average Price'], label='Ground Truth', color='blue')
        plt.plot(df['Date'], df['MA_7'], label='MA 7', color='orange')
        plt.plot(df['Date'], df['MA_30'], label='MA 30', color='green')
        plt.plot(df['Date'], df['Predicted'], label='Predicted (TAT)', color='red', linestyle='dashed')
        plt.xlabel('Date')
        plt.ylabel('Average Price')
        plt.title(f'Price Prediction (TAT) - {file}')
        plt.legend()
        plt.grid(True)
        graph_file = os.path.join(output_graphs, file.replace(".csv", "_tat_graph.png"))
        plt.savefig(graph_file)
        plt.close()

        print(f"✅ Done with {file} | MAE={mae}, RMSE={rmse}, R2={r2}, MAPE={mape}%, Accuracy={accuracy}%\n")

# Save all metrics
metrics_df = pd.DataFrame(metrics_list, columns=['District', 'MAE', 'RMSE', 'R2', 'MAPE(%)', 'Accuracy(%)'])
metrics_df.to_csv(metrics_file, index=False)
print(f"📊 Metrics saved to {metrics_file}")

🚀 Processing: wheat_Bagalkot_weekly.csv


Model: "functional"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                  ┃ Output Shape              ┃         Param # ┃ Connected to               ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ input_layer (InputLayer)      │ (None, 30, 1)             │               0 │ -                          │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ multi_head_attention          │ (None, 30, 1)             │           1,793 │ input_layer[0][0],         │
│ (MultiHeadAttention)          │                           │                 │ input_layer[0][0]          │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dropout_1 (Dropout)           │ (None, 30, 1)             │               0 │ multi_head_attention[0][0] │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add (Add)                     │ (None, 30, 1)             │               0 │ dropout_1[0][0],           │
│                               │                           │                 │ input_layer[0][0]          │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization           │ (None, 30, 1)             │               2 │ add[0][0]                  │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense (Dense)                 │ (None, 30, 128)           │             256 │ layer_normalization[0][0]  │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_1 (Dense)               │ (None, 30, 1)             │             129 │ dense[0][0]                │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_1 (Add)                   │ (None, 30, 1)             │               0 │ layer_normalization[0][0], │
│                               │                           │                 │ dense_1[0][0]              │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_1         │ (None, 30, 1)             │               2 │ add_1[0][0]                │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ global_average_pooling1d      │ (None, 1)                 │               0 │ layer_normalization_1[0][… │
│ (GlobalAveragePooling1D)      │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_2 (Dense)               │ (None, 1)                 │               2 │ global_average_pooling1d[… │
└───────────────────────────────┴───────────────────────────┴─────────────────┴────────────────────────────┘

 Total params: 2,184 (8.53 KB)

 Trainable params: 2,184 (8.53 KB)

...

 Total params: 2,184 (8.53 KB)

 Trainable params: 2,184 (8.53 KB)

 Non-trainable params: 0 (0.00 B)

Epoch 1/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 7s 30ms/step - loss: 0.0088 - mae: 0.0772 - val_loss: 0.0370 - val_mae: 0.1437
Epoch 2/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 1s 11ms/step - loss: 0.0037 - mae: 0.0488 - val_loss: 0.0280 - val_mae: 0.1078
Epoch 3/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 1s 11ms/step - loss: 0.0030 - mae: 0.0400 - val_loss: 0.0259 - val_mae: 0.0978
Epoch 4/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0030 - mae: 0.0395 - val_loss: 0.0259 - val_mae: 0.0980
Epoch 5/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 0.0030 - mae: 0.0397 - val_loss: 0.0261 - val_mae: 0.0988
Epoch 6/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0030 - mae: 0.0397 - val_loss: 0.0261 - val_mae: 0.0987
Epoch 7/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - loss: 0.0030 - mae: 0.0397 - val_loss: 0.0261 - val_mae: 0.0988
Epoch 8/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - loss: 0.0030 - mae: 0.0397 - val_loss: 0.0262 - val_mae: 0.0992
Epoch 9/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - lo

✅ Done with wheat_Tumkur_weekly.csv | MAE=464.57, RMSE=793.17, R2=-0.04, MAPE=18.35%, Accuracy=81.65%

📊 Metrics saved to tat_metrics.csv


In [ ]:
#TAT + MQA

In [6]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import tensorflow as tf
from tensorflow.keras import layers, models, optimizers

# -----------------------------
# Output directories
# -----------------------------
input_folder = "dataset"
output_models = "tat_mqa_output_models"
output_csv = "tat_mqa_output_csv"
output_graphs = "tat_mqa_output_graphs"
output_logs = "tat_mqa_output_logs"
metrics_file = "tat_mqa_metrics.csv"

os.makedirs(output_models, exist_ok=True)
os.makedirs(output_csv, exist_ok=True)
os.makedirs(output_graphs, exist_ok=True)
os.makedirs(output_logs, exist_ok=True)

# -----------------------------
# Function to create dataset
# -----------------------------
def create_dataset(data, look_back=30):
    X, y = [], []
    for i in range(len(data) - look_back):
        X.append(data[i:i+look_back, 0])
        y.append(data[i+look_back, 0])
    return np.array(X), np.array(y)

# -----------------------------
# Multi-Query Attention Layer
# -----------------------------
class MultiQueryAttention(layers.Layer):
    def __init__(self, num_heads, key_dim, dropout_rate=0.1, **kwargs):
        super(MultiQueryAttention, self).__init__(**kwargs)
        self.num_heads = num_heads
        self.key_dim = key_dim
        self.dropout_rate = dropout_rate
        self.q_dense = [layers.Dense(key_dim) for _ in range(num_heads)]
        self.k_dense = layers.Dense(key_dim)
        self.v_dense = layers.Dense(key_dim)
        self.dropout = layers.Dropout(dropout_rate)
        self.output_dense = layers.Dense(key_dim)

    def call(self, x):
        K = self.k_dense(x)
        V = self.v_dense(x)
        head_outputs = []

        for q_layer in self.q_dense:
            Q = q_layer(x)
            scores = tf.matmul(Q, K, transpose_b=True) / tf.math.sqrt(tf.cast(self.key_dim, tf.float32))
            attention_weights = tf.nn.softmax(scores, axis=-1)
            attention_output = tf.matmul(attention_weights, V)
            head_outputs.append(attention_output)

        concat = tf.concat(head_outputs, axis=-1)
        output = self.output_dense(concat)
        output = self.dropout(output)
        return output

    def get_config(self):
        config = super(MultiQueryAttention, self).get_config()
        config.update({
            "num_heads": self.num_heads,
            "key_dim": self.key_dim,
            "dropout_rate": self.dropout_rate
        })
        return config

# -----------------------------
# TAT-MQA Model
# -----------------------------
def build_tat_mqa_model(input_shape, d_model=64, num_heads=4, ff_dim=128, dropout_rate=0.2):
    inputs = layers.Input(shape=input_shape)
    x = MultiQueryAttention(num_heads=num_heads, key_dim=d_model, dropout_rate=dropout_rate)(inputs)
    x = layers.LayerNormalization(epsilon=1e-6)(x + inputs)

    ff = layers.Dense(ff_dim, activation='relu')(x)
    ff = layers.Dense(input_shape[1])(ff)
    x = layers.LayerNormalization(epsilon=1e-6)(x + ff)

    x = layers.GlobalAveragePooling1D()(x)
    outputs = layers.Dense(1)(x)

    model = models.Model(inputs=inputs, outputs=outputs)
    model.compile(optimizer=optimizers.Adam(learning_rate=0.001),
                  loss='mse', metrics=['mae'])
    return model

# -----------------------------
# Metrics storage
# -----------------------------
metrics_list = []

# -----------------------------
# Process each CSV file
# -----------------------------
look_back = 30
for file in os.listdir(input_folder):
    if file.endswith(".csv"):
        file_path = os.path.join(input_folder, file)
        print(f"🚀 Processing: {file}")

        # Load CSV
        df = pd.read_csv(file_path)

        # Handle multiple date formats
        try:
            df['Date'] = pd.to_datetime(df['Date'], infer_datetime_format=True, errors='coerce')
        except Exception as e:
            print(f"Date conversion failed: {e}")
            continue

        df = df.dropna(subset=['Date'])
        df = df.sort_values('Date')

        # Handle NaNs
        df['Average Price'].fillna(df['Average Price'].mean(), inplace=True)

        # Moving averages
        df['MA_7'] = df['Average Price'].rolling(window=7).mean()
        df['MA_30'] = df['Average Price'].rolling(window=30).mean()
        df['MA_7'].fillna(df['MA_7'].mean(), inplace=True)
        df['MA_30'].fillna(df['MA_30'].mean(), inplace=True)

        # Prepare data
        values = df[['Average Price']].values.astype('float32')
        scaler = MinMaxScaler(feature_range=(0, 1))
        scaled_values = scaler.fit_transform(values)
        X, y = create_dataset(scaled_values, look_back)
        X = np.reshape(X, (X.shape[0], X.shape[1], 1))

        # Build model
        model = build_tat_mqa_model(input_shape=(look_back,1))
        model.summary()

        # Train model
        history = model.fit(X, y, epochs=100, batch_size=16, validation_split=0.2, verbose=1)

        # Save logs
        log_file = os.path.join(output_logs, file.replace(".csv", "_tat_mqa_training.txt"))
        with open(log_file, "w") as f:
            f.write("Training Loss per Epoch:\n")
            for i, loss in enumerate(history.history['loss']):
                f.write(f"Epoch {i+1}: Loss={loss}, Val_Loss={history.history['val_loss'][i]}\n")

        # Predictions
        predictions = model.predict(X)
        predictions_rescaled = scaler.inverse_transform(predictions)
        df['Predicted'] = [np.nan]*look_back + list(predictions_rescaled.flatten())

        # Round Actual and Predicted
        df['Average Price'] = df['Average Price'].round(2)
        df['Predicted'] = df['Predicted'].round(2)

        # Metrics
        y_true = df['Average Price'].values[look_back:]
        y_pred = predictions_rescaled.flatten()
        mae = round(mean_absolute_error(y_true, y_pred), 2)
        rmse = round(np.sqrt(mean_squared_error(y_true, y_pred)), 2)
        r2 = round(r2_score(y_true, y_pred), 2)
        mape = round(np.mean(np.abs((y_true - y_pred) / y_true)) * 100, 2)
        accuracy = round(100 - mape, 2)
        metrics_list.append([file.replace(".csv",""), mae, rmse, r2, mape, accuracy])

        # Save model
        model_file = os.path.join(output_models, file.replace(".csv", "_tat_mqa_model.keras"))
        model.save(model_file)

        # Save CSV
        updated_csv_path = os.path.join(output_csv, file.replace(".csv", "_tat_mqa_updated.csv"))
        df.to_csv(updated_csv_path, index=False)

        # Save graph
        plt.figure(figsize=(12,6))
        plt.plot(df['Date'], df['Average Price'], label='Ground Truth', color='blue')
        plt.plot(df['Date'], df['MA_7'], label='MA 7', color='orange')
        plt.plot(df['Date'], df['MA_30'], label='MA 30', color='green')
        plt.plot(df['Date'], df['Predicted'], label='Predicted (TAT-MQA)', color='red', linestyle='dashed')
        plt.xlabel('Date')
        plt.ylabel('Average Price')
        plt.title(f'Price Prediction (TAT-MQA) - {file}')
        plt.legend()
        plt.grid(True)
        graph_file = os.path.join(output_graphs, file.replace(".csv", "_tat_mqa_graph.png"))
        plt.savefig(graph_file)
        plt.close()

        print(f"✅ Done with {file} | MAE={mae}, RMSE={rmse}, R2={r2}, MAPE={mape}%, Accuracy={accuracy}%\n")

# Save metrics
metrics_df = pd.DataFrame(metrics_list, columns=['District', 'MAE', 'RMSE', 'R2', 'MAPE(%)', 'Accuracy(%)'])
metrics_df.to_csv(metrics_file, index=False)
print(f"📊 Metrics saved to {metrics_file}")

🚀 Processing: wheat_Bagalkot_weekly.csv



Model: "functional_22"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                  ┃ Output Shape              ┃         Param # ┃ Connected to               ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ input_layer_22 (InputLayer)   │ (None, 30, 1)             │               0 │ -                          │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ multi_query_attention         │ (None, 30, 64)            │          17,216 │ input_layer_22[0][0]       │
│ (MultiQueryAttention)         │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_44 (Add)                  │ (None, 30, 64)            │               0 │ multi_query_attention[0][… │
│                               │                           │                 │ input_layer_22[0][0]       │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_44        │ (None, 30, 64)            │             128 │ add_44[0][0]               │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_73 (Dense)              │ (None, 30, 128)           │           8,320 │ layer_normalization_44[0]… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_74 (Dense)              │ (None, 30, 1)             │             129 │ dense_73[0][0]             │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_45 (Add)                  │ (None, 30, 64)            │               0 │ layer_normalization_44[0]… │
│                               │                           │                 │ dense_74[0][0]             │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_45        │ (None, 30, 64)            │             128 │ add_45[0][0]               │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ global_average_pooling1d_22   │ (None, 64)                │               0 │ layer_normalization_45[0]… │
│ (GlobalAveragePooling1D)      │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_75 (Dense)              │ (None, 1)                 │              65 │ global_average_pooling1d_… │
└───────────────────────────────┴───────────────────────────┴─────────────────┴────────────────────────────┘

 Total params: 25,986 (101.51 KB)

 Trainable params: 25,986 (101.51 KB)

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                  ┃ Output Shape              ┃         Param # ┃ Connected to               ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ input_layer_43 (InputLayer)   │ (None, 30, 1)             │               0 │ -                          │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ multi_query_attention_21      │ (None, 30, 64)            │          17,216 │ input_layer_43[0][0]       │
│ (MultiQueryAttention)         │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_86 (Add)                  │ (None, 30, 64)            │               0 │ multi_query_attention_21[… │
│                               │                           │                 │ input_layer_43[0][0]       │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_86        │ (None, 30, 64)            │             128 │ add_86[0][0]               │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_283 (Dense)             │ (None, 30, 128)           │           8,320 │ layer_normalization_86[0]… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_284 (Dense)             │ (None, 30, 1)             │             129 │ dense_283[0][0]            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_87 (Add)                  │ (None, 30, 64)            │               0 │ layer_normalization_86[0]… │
│                               │                           │                 │ dense_284[0][0]            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_87        │ (None, 30, 64)            │             128 │ add_87[0][0]               │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ global_average_pooling1d_43   │ (None, 64)                │               0 │ layer_normalization_87[0]… │
│ (GlobalAveragePooling1D)      │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_285 (Dense)             │ (None, 1)                 │              65 │ global_average_pooling1d_… │
└───────────────────────────────┴───────────────────────────┴─────────────────┴────────────────────────────┘

 Total params: 25,986 (101.51 KB)

 Trainable params: 25,986 (101.51 KB)

 Non-trainable params: 0 (0.00 B)

Epoch 1/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 11s 33ms/step - loss: 0.4494 - mae: 0.4471 - val_loss: 0.0202 - val_mae: 0.0769
Epoch 2/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0134 - mae: 0.0923 - val_loss: 0.0167 - val_mae: 0.0497
Epoch 3/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step - loss: 0.0124 - mae: 0.0885 - val_loss: 0.0158 - val_mae: 0.0746
Epoch 4/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0119 - mae: 0.0870 - val_loss: 0.0184 - val_mae: 0.0586
Epoch 5/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0111 - mae: 0.0842 - val_loss: 0.0152 - val_mae: 0.0509
Epoch 6/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0116 - mae: 0.0863 - val_loss: 0.0157 - val_mae: 0.0464
Epoch 7/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0094 - mae: 0.0782 - val_loss: 0.0162 - val_mae: 0.0743
Epoch 8/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0098 - mae: 0.0796 - val_loss: 0.0160 - val_mae: 0.0714
Epoch 9/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - l

In [ ]:
#TAT+GQA

In [7]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import tensorflow as tf
from tensorflow.keras import layers, models, optimizers

# -----------------------------
# Output directories
# -----------------------------
input_folder = "dataset"
output_models = "tat_gqa_output_models"
output_csv = "tat_gqa_output_csv"
output_graphs = "tat_gqa_output_graphs"
output_logs = "tat_gqa_output_logs"
metrics_file = "tat_gqa_metrics.csv"

os.makedirs(output_models, exist_ok=True)
os.makedirs(output_csv, exist_ok=True)
os.makedirs(output_graphs, exist_ok=True)
os.makedirs(output_logs, exist_ok=True)

# -----------------------------
# Function to create dataset
# -----------------------------
def create_dataset(data, look_back=30):
    X, y = [], []
    for i in range(len(data) - look_back):
        X.append(data[i:i+look_back, 0])
        y.append(data[i+look_back, 0])
    return np.array(X), np.array(y)

# -----------------------------
# Grouped Query Attention Layer
# -----------------------------
class GroupedQueryAttention(layers.Layer):
    def __init__(self, num_groups=2, key_dim=64, dropout_rate=0.1, **kwargs):
        super(GroupedQueryAttention, self).__init__(**kwargs)
        self.num_groups = num_groups
        self.key_dim = key_dim
        self.dropout_rate = dropout_rate
        self.k_dense = layers.Dense(key_dim)
        self.v_dense = layers.Dense(key_dim)
        self.q_dense_groups = [layers.Dense(key_dim) for _ in range(num_groups)]
        self.dropout = layers.Dropout(dropout_rate)
        self.output_dense = layers.Dense(key_dim)

    def call(self, x):
        K = self.k_dense(x)
        V = self.v_dense(x)
        group_outputs = []
        for q_layer in self.q_dense_groups:
            Q = q_layer(x)
            scores = tf.matmul(Q, K, transpose_b=True) / tf.math.sqrt(tf.cast(self.key_dim, tf.float32))
            attention_weights = tf.nn.softmax(scores, axis=-1)
            attn_output = tf.matmul(attention_weights, V)
            group_outputs.append(attn_output)
        concat = tf.concat(group_outputs, axis=-1)
        output = self.output_dense(concat)
        output = self.dropout(output)
        return output

    def get_config(self):
        config = super(GroupedQueryAttention, self).get_config()
        config.update({
            "num_groups": self.num_groups,
            "key_dim": self.key_dim,
            "dropout_rate": self.dropout_rate
        })
        return config

# -----------------------------
# TAT-GQA Model
# -----------------------------
def build_tat_gqa_model(input_shape, d_model=64, num_groups=2, ff_dim=128, dropout_rate=0.2):
    inputs = layers.Input(shape=input_shape)
    x = GroupedQueryAttention(num_groups=num_groups, key_dim=d_model, dropout_rate=dropout_rate)(inputs)
    x = layers.LayerNormalization(epsilon=1e-6)(x + inputs)
    ff = layers.Dense(ff_dim, activation='relu')(x)
    ff = layers.Dense(input_shape[1])(ff)
    x = layers.LayerNormalization(epsilon=1e-6)(x + ff)
    x = layers.GlobalAveragePooling1D()(x)
    outputs = layers.Dense(1)(x)
    model = models.Model(inputs=inputs, outputs=outputs)
    model.compile(optimizer=optimizers.Adam(learning_rate=0.001),
                  loss='mse', metrics=['mae'])
    return model

# -----------------------------
# Metrics storage
# -----------------------------
metrics_list = []

# -----------------------------
# Process each CSV file
# -----------------------------
look_back = 30
for file in os.listdir(input_folder):
    if file.endswith(".csv"):
        file_path = os.path.join(input_folder, file)
        print(f"🚀 Processing: {file}")

        # Load CSV
        df = pd.read_csv(file_path)

        # Handle multiple date formats
        try:
            df['Date'] = pd.to_datetime(df['Date'], infer_datetime_format=True, errors='coerce')
        except Exception as e:
            print(f"Date conversion failed: {e}")
            continue

        df = df.dropna(subset=['Date'])
        df = df.sort_values('Date')

        # Handle NaNs
        df['Average Price'].fillna(df['Average Price'].mean(), inplace=True)

        # Moving averages
        df['MA_7'] = df['Average Price'].rolling(window=7).mean()
        df['MA_30'] = df['Average Price'].rolling(window=30).mean()
        df['MA_7'].fillna(df['MA_7'].mean(), inplace=True)
        df['MA_30'].fillna(df['MA_30'].mean(), inplace=True)

        # Prepare data
        values = df[['Average Price']].values.astype('float32')
        scaler = MinMaxScaler(feature_range=(0, 1))
        scaled_values = scaler.fit_transform(values)
        X, y = create_dataset(scaled_values, look_back)
        X = np.reshape(X, (X.shape[0], X.shape[1], 1))

        # Build model
        model = build_tat_gqa_model(input_shape=(look_back,1), num_groups=2)
        model.summary()

        # Train model
        history = model.fit(X, y, epochs=100, batch_size=16, validation_split=0.2, verbose=1)

        # Save logs
        log_file = os.path.join(output_logs, file.replace(".csv", "_tat_gqa_training.txt"))
        with open(log_file, "w") as f:
            f.write("Training Loss per Epoch:\n")
            for i, loss in enumerate(history.history['loss']):
                f.write(f"Epoch {i+1}: Loss={loss}, Val_Loss={history.history['val_loss'][i]}\n")

        # Predictions
        predictions = model.predict(X)
        predictions_rescaled = scaler.inverse_transform(predictions)
        df['Predicted'] = [np.nan]*look_back + list(predictions_rescaled.flatten())

        # Round Actual and Predicted
        df['Average Price'] = df['Average Price'].round(2)
        df['Predicted'] = df['Predicted'].round(2)

        # Metrics
        y_true = df['Average Price'].values[look_back:]
        y_pred = predictions_rescaled.flatten()
        mae = round(mean_absolute_error(y_true, y_pred), 2)
        rmse = round(np.sqrt(mean_squared_error(y_true, y_pred)), 2)
        r2 = round(r2_score(y_true, y_pred), 2)
        mape = round(np.mean(np.abs((y_true - y_pred) / y_true)) * 100, 2)
        accuracy = round(100 - mape, 2)
        metrics_list.append([file.replace(".csv",""), mae, rmse, r2, mape, accuracy])

        # Save model
        model_file = os.path.join(output_models, file.replace(".csv", "_tat_gqa_model.keras"))
        model.save(model_file)

        # Save CSV
        updated_csv_path = os.path.join(output_csv, file.replace(".csv", "_tat_gqa_updated.csv"))
        df.to_csv(updated_csv_path, index=False)

        # Save graph
        plt.figure(figsize=(12,6))
        plt.plot(df['Date'], df['Average Price'], label='Ground Truth', color='blue')
        plt.plot(df['Date'], df['MA_7'], label='MA 7', color='orange')
        plt.plot(df['Date'], df['MA_30'], label='MA 30', color='green')
        plt.plot(df['Date'], df['Predicted'], label='Predicted (TAT-GQA)', color='red', linestyle='dashed')
        plt.xlabel('Date')
        plt.ylabel('Average Price')
        plt.title(f'Price Prediction (TAT-GQA) - {file}')
        plt.legend()
        plt.grid(True)
        graph_file = os.path.join(output_graphs, file.replace(".csv", "_tat_gqa_graph.png"))
        plt.savefig(graph_file)
        plt.close()

        print(f"✅ Done with {file} | MAE={mae}, RMSE={rmse}, R2={r2}, MAPE={mape}%, Accuracy={accuracy}%\n")

# Save metrics
metrics_df = pd.DataFrame(metrics_list, columns=['District', 'MAE', 'RMSE', 'R2', 'MAPE(%)', 'Accuracy(%)'])
metrics_df.to_csv(metrics_file, index=False)
print(f"📊 Metrics saved to {metrics_file}")

🚀 Processing: wheat_Bagalkot_weekly.csv


Model: "functional_44"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                  ┃ Output Shape              ┃         Param # ┃ Connected to               ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ input_layer_44 (InputLayer)   │ (None, 30, 1)             │               0 │ -                          │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ grouped_query_attention       │ (None, 30, 64)            │           8,768 │ input_layer_44[0][0]       │
│ (GroupedQueryAttention)       │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_88 (Add)                  │ (None, 30, 64)            │               0 │ grouped_query_attention[0… │
│                               │                           │                 │ input_layer_44[0][0]       │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_88        │ (None, 30, 64)            │             128 │ add_88[0][0]               │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_291 (Dense)             │ (None, 30, 128)           │           8,320 │ layer_normalization_88[0]… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_292 (Dense)             │ (None, 30, 1)             │             129 │ dense_291[0][0]            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_89 (Add)                  │ (None, 30, 64)            │               0 │ layer_normalization_88[0]… │
│                               │                           │                 │ dense_292[0][0]            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_89        │ (None, 30, 64)            │             128 │ add_89[0][0]               │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ global_average_pooling1d_44   │ (None, 64)                │               0 │ layer_normalization_89[0]… │
│ (GlobalAveragePooling1D)      │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_293 (Dense)             │ (None, 1)                 │              65 │ global_average_pooling1d_… │
└───────────────────────────────┴───────────────────────────┴─────────────────┴────────────────────────────┘

 Total params: 17,538 (68.51 KB)

 Trainable params: 17,538 (68.51 KB)

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                  ┃ Output Shape              ┃         Param # ┃ Connected to               ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ input_layer_65 (InputLayer)   │ (None, 30, 1)             │               0 │ -                          │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ grouped_query_attention_21    │ (None, 30, 64)            │           8,768 │ input_layer_65[0][0]       │
│ (GroupedQueryAttention)       │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_130 (Add)                 │ (None, 30, 64)            │               0 │ grouped_query_attention_2… │
│                               │                           │                 │ input_layer_65[0][0]       │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_130       │ (None, 30, 64)            │             128 │ add_130[0][0]              │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_459 (Dense)             │ (None, 30, 128)           │           8,320 │ layer_normalization_130[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_460 (Dense)             │ (None, 30, 1)             │             129 │ dense_459[0][0]            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_131 (Add)                 │ (None, 30, 64)            │               0 │ layer_normalization_130[0… │
│                               │                           │                 │ dense_460[0][0]            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_131       │ (None, 30, 64)            │             128 │ add_131[0][0]              │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ global_average_pooling1d_65   │ (None, 64)                │               0 │ layer_normalization_131[0… │
│ (GlobalAveragePooling1D)      │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_461 (Dense)             │ (None, 1)                 │              65 │ global_average_pooling1d_… │
└───────────────────────────────┴───────────────────────────┴─────────────────┴────────────────────────────┘

 Total params: 17,538 (68.51 KB)

 Trainable params: 17,538 (68.51 KB)

 Non-trainable params: 0 (0.00 B)

Epoch 1/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 8s 30ms/step - loss: 0.8681 - mae: 0.6132 - val_loss: 0.0256 - val_mae: 0.1059
Epoch 2/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0194 - mae: 0.1126 - val_loss: 0.0164 - val_mae: 0.0458
Epoch 3/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0124 - mae: 0.0892 - val_loss: 0.0154 - val_mae: 0.0455
Epoch 4/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step - loss: 0.0112 - mae: 0.0858 - val_loss: 0.0151 - val_mae: 0.0472
Epoch 5/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step - loss: 0.0102 - mae: 0.0801 - val_loss: 0.0152 - val_mae: 0.0463
Epoch 6/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - loss: 0.0095 - mae: 0.0764 - val_loss: 0.0147 - val_mae: 0.0474
Epoch 7/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - loss: 0.0099 - mae: 0.0784 - val_loss: 0.0156 - val_mae: 0.0445
Epoch 8/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0082 - mae: 0.0722 - val_loss: 0.0154 - val_mae: 0.0459
Epoch 9/100
34/34 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step - lo

In [ ]:
#TAT+HA

In [8]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import joblib
import tensorflow as tf
from tensorflow.keras import layers, models, optimizers

# -----------------------------
# Output directories
# -----------------------------
input_folder = "dataset"
output_models = "tat_ha_output_models"
output_csv = "tat_ha_output_csv"
output_graphs = "tat_ha_output_graphs"
output_logs = "tat_ha_output_logs"
metrics_file = "tat_ha_metrics.csv"

os.makedirs(output_models, exist_ok=True)
os.makedirs(output_csv, exist_ok=True)
os.makedirs(output_graphs, exist_ok=True)
os.makedirs(output_logs, exist_ok=True)

# -----------------------------
# Function to create dataset
# -----------------------------
def create_dataset(data, look_back=30):
    X, y = [], []
    for i in range(len(data) - look_back):
        X.append(data[i:i+look_back, 0])
        y.append(data[i+look_back, 0])
    return np.array(X), np.array(y)

# -----------------------------
# Local Attention Layer
# -----------------------------
class LocalAttention(layers.Layer):
    def __init__(self, key_dim=64, dropout_rate=0.1, **kwargs):
        super(LocalAttention, self).__init__(**kwargs)
        self.key_dim = key_dim
        self.dropout_rate = dropout_rate
        self.q_dense = layers.Dense(key_dim)
        self.k_dense = layers.Dense(key_dim)
        self.v_dense = layers.Dense(key_dim)
        self.dropout = layers.Dropout(dropout_rate)

    def call(self, x):
        Q = self.q_dense(x)
        K = self.k_dense(x)
        V = self.v_dense(x)
        scores = tf.matmul(Q, K, transpose_b=True) / tf.math.sqrt(tf.cast(tf.shape(K)[-1], tf.float32))
        weights = tf.nn.softmax(scores, axis=-1)
        output = tf.matmul(weights, V)
        output = self.dropout(output)
        return output

# -----------------------------
# Hierarchical Attention Model
# -----------------------------
def build_tat_ha_model(input_shape, d_model=64, ff_dim=128, dropout_rate=0.2):
    inputs = layers.Input(shape=input_shape)
    local_attn = LocalAttention(key_dim=d_model, dropout_rate=dropout_rate)(inputs)
    local_attn = layers.LayerNormalization(epsilon=1e-6)(local_attn + inputs)
    global_attn = layers.MultiHeadAttention(num_heads=4, key_dim=d_model)(local_attn, local_attn)
    global_attn = layers.Dropout(dropout_rate)(global_attn)
    global_attn = layers.LayerNormalization(epsilon=1e-6)(global_attn + local_attn)
    ff = layers.Dense(ff_dim, activation='relu')(global_attn)
    ff = layers.Dense(input_shape[1])(ff)
    x = layers.LayerNormalization(epsilon=1e-6)(ff + global_attn)
    x = layers.GlobalAveragePooling1D()(x)
    outputs = layers.Dense(1)(x)
    model = models.Model(inputs=inputs, outputs=outputs)
    model.compile(optimizer=optimizers.Adam(learning_rate=0.001),
                  loss='mse', metrics=['mae'])
    return model

# -----------------------------
# Metrics storage
# -----------------------------
metrics_list = []

# -----------------------------
# Process each CSV file
# -----------------------------
look_back = 30
for file in os.listdir(input_folder):
    if file.endswith(".csv"):
        file_path = os.path.join(input_folder, file)
        print(f"🚀 Processing: {file}")

        # Load CSV
        df = pd.read_csv(file_path)

        # Handle multiple date formats
        df['Date'] = pd.to_datetime(df['Date'], infer_datetime_format=True, errors='coerce')
        df = df.dropna(subset=['Date'])
        df = df.sort_values('Date')

        # Handle missing Average Price
        df['Average Price'].fillna(df['Average Price'].mean(), inplace=True)

        # Moving averages
        df['MA_7'] = df['Average Price'].rolling(window=7).mean()
        df['MA_30'] = df['Average Price'].rolling(window=30).mean()
        df['MA_7'].fillna(df['MA_7'].mean(), inplace=True)
        df['MA_30'].fillna(df['MA_30'].mean(), inplace=True)

        # Prepare data
        values = df[['Average Price']].values.astype('float32')
        scaler = MinMaxScaler(feature_range=(0, 1))
        scaled_values = scaler.fit_transform(values)
        X, y = create_dataset(scaled_values, look_back)
        X = np.reshape(X, (X.shape[0], X.shape[1], 1))

        # Build model
        model = build_tat_ha_model(input_shape=(look_back,1))
        model.summary()

        # Train model
        history = model.fit(X, y, epochs=50, batch_size=16, validation_split=0.2, verbose=1)

        # Save logs
        log_file = os.path.join(output_logs, file.replace(".csv", "_tat_ha_training.txt"))
        with open(log_file, "w") as f:
            f.write("Training Loss per Epoch:\n")
            for i, loss in enumerate(history.history['loss']):
                f.write(f"Epoch {i+1}: Loss={loss}, Val_Loss={history.history['val_loss'][i]}\n")

        # Predictions
        predictions = model.predict(X)
        predictions_rescaled = scaler.inverse_transform(predictions)
        df['Predicted'] = [np.nan]*look_back + list(predictions_rescaled.flatten())

        # Round Actual & Predicted
        df['Average Price'] = df['Average Price'].round(2)
        df['Predicted'] = df['Predicted'].round(2)

        # Metrics
        y_true = df['Average Price'].values[look_back:]
        y_pred = predictions_rescaled.flatten()
        mae = round(mean_absolute_error(y_true, y_pred), 2)
        rmse = round(np.sqrt(mean_squared_error(y_true, y_pred)), 2)
        r2 = round(r2_score(y_true, y_pred), 2)
        mape = round(np.mean(np.abs((y_true - y_pred)/y_true))*100, 2)
        accuracy = round(100 - mape, 2)
        metrics_list.append([file.replace(".csv",""), mae, rmse, r2, mape, accuracy])

        # Save model as .pkl
        model_file = os.path.join(output_models, file.replace(".csv", "_tat_ha_model.pkl"))
        joblib.dump(model, model_file)

        # Save CSV
        updated_csv_path = os.path.join(output_csv, file.replace(".csv", "_tat_ha_updated.csv"))
        df.to_csv(updated_csv_path, index=False)

        # Save graph
        plt.figure(figsize=(12,6))
        plt.plot(df['Date'], df['Average Price'], label='Ground Truth', color='blue')
        plt.plot(df['Date'], df['MA_7'], label='MA 7', color='orange')
        plt.plot(df['Date'], df['MA_30'], label='MA 30', color='green')
        plt.plot(df['Date'], df['Predicted'], label='Predicted (TAT-HA)', color='red', linestyle='dashed')
        plt.xlabel('Date')
        plt.ylabel('Average Price')
        plt.title(f'Price Prediction (TAT-HA) - {file}')
        plt.legend()
        plt.grid(True)
        graph_file = os.path.join(output_graphs, file.replace(".csv", "_tat_ha_graph.png"))
        plt.savefig(graph_file)
        plt.close()

        print(f"✅ Done with {file} | MAE={mae}, RMSE={rmse}, R2={r2}, MAPE={mape}%, Accuracy={accuracy}%\n")

# Save metrics
metrics_df = pd.DataFrame(metrics_list, columns=['District', 'MAE', 'RMSE', 'R2', 'MAPE(%)', 'Accuracy(%)'])
metrics_df.to_csv(metrics_file, index=False)
print(f"📊 Metrics saved to {metrics_file}")

🚀 Processing: wheat_Bagalkot_weekly.csv


Model: "functional_66"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                  ┃ Output Shape              ┃         Param # ┃ Connected to               ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ input_layer_66 (InputLayer)   │ (None, 30, 1)             │               0 │ -                          │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ local_attention               │ (None, 30, 64)            │             384 │ input_layer_66[0][0]       │
│ (LocalAttention)              │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_132 (Add)                 │ (None, 30, 64)            │               0 │ local_attention[0][0],     │
│                               │                           │                 │ input_layer_66[0][0]       │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_132       │ (None, 30, 64)            │             128 │ add_132[0][0]              │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ multi_head_attention_22       │ (None, 30, 64)            │          66,368 │ layer_normalization_132[0… │
│ (MultiHeadAttention)          │                           │                 │ layer_normalization_132[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dropout_90 (Dropout)          │ (None, 30, 64)            │               0 │ multi_head_attention_22[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_133 (Add)                 │ (None, 30, 64)            │               0 │ dropout_90[0][0],          │
│                               │                           │                 │ layer_normalization_132[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_133       │ (None, 30, 64)            │             128 │ add_133[0][0]              │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_465 (Dense)             │ (None, 30, 128)           │           8,320 │ layer_normalization_133[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_466 (Dense)             │ (None, 30, 1)             │             129 │ dense_465[0][0]            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_134 (Add)                 │ (None, 30, 64)            │               0 │ dense_466[0][0],           │
│                               │                           │                 │ layer_normalization_133[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_134       │ (None, 30, 64)            │             128 │ add_134[0][0]              │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ global_average_pooling1d_66   │ (None, 64)                │               0 │ layer_normalization_134[0… │
│ (GlobalAveragePooling1D)      │                           │               

 Total params: 75,650 (295.51 KB)

 Trainable params: 75,650 (295.51 KB)

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                  ┃ Output Shape              ┃         Param # ┃ Connected to               ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ input_layer_87 (InputLayer)   │ (None, 30, 1)             │               0 │ -                          │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ local_attention_21            │ (None, 30, 64)            │             384 │ input_layer_87[0][0]       │
│ (LocalAttention)              │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_195 (Add)                 │ (None, 30, 64)            │               0 │ local_attention_21[0][0],  │
│                               │                           │                 │ input_layer_87[0][0]       │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_195       │ (None, 30, 64)            │             128 │ add_195[0][0]              │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ multi_head_attention_43       │ (None, 30, 64)            │          66,368 │ layer_normalization_195[0… │
│ (MultiHeadAttention)          │                           │                 │ layer_normalization_195[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dropout_153 (Dropout)         │ (None, 30, 64)            │               0 │ multi_head_attention_43[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_196 (Add)                 │ (None, 30, 64)            │               0 │ dropout_153[0][0],         │
│                               │                           │                 │ layer_normalization_195[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_196       │ (None, 30, 64)            │             128 │ add_196[0][0]              │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_591 (Dense)             │ (None, 30, 128)           │           8,320 │ layer_normalization_196[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ dense_592 (Dense)             │ (None, 30, 1)             │             129 │ dense_591[0][0]            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ add_197 (Add)                 │ (None, 30, 64)            │               0 │ dense_592[0][0],           │
│                               │                           │                 │ layer_normalization_196[0… │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ layer_normalization_197       │ (None, 30, 64)            │             128 │ add_197[0][0]              │
│ (LayerNormalization)          │                           │                 │                            │
├───────────────────────────────┼───────────────────────────┼─────────────────┼────────────────────────────┤
│ global_average_pooling1d_87   │ (None, 64)                │               0 │ layer_normalization_197[0… │
│ (GlobalAveragePooling1D)      │                           │               

 Total params: 75,650 (295.51 KB)

 Trainable params: 75,650 (295.51 KB)

 Non-trainable params: 0 (0.00 B)

Epoch 1/50
34/34 ━━━━━━━━━━━━━━━━━━━━ 13s 49ms/step - loss: 0.2034 - mae: 0.3217 - val_loss: 0.0162 - val_mae: 0.0709
Epoch 2/50
34/34 ━━━━━━━━━━━━━━━━━━━━ 2s 32ms/step - loss: 0.0085 - mae: 0.0709 - val_loss: 0.0168 - val_mae: 0.0487
Epoch 3/50
34/34 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - loss: 0.0051 - mae: 0.0568 - val_loss: 0.0203 - val_mae: 0.0685
Epoch 4/50
34/34 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - loss: 0.0051 - mae: 0.0576 - val_loss: 0.0182 - val_mae: 0.0555
Epoch 5/50
34/34 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - loss: 0.0048 - mae: 0.0536 - val_loss: 0.0169 - val_mae: 0.0498
Epoch 6/50
34/34 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - loss: 0.0046 - mae: 0.0529 - val_loss: 0.0163 - val_mae: 0.0495
Epoch 7/50
34/34 ━━━━━━━━━━━━━━━━━━━━ 1s 37ms/step - loss: 0.0040 - mae: 0.0489 - val_loss: 0.0171 - val_mae: 0.0496
Epoch 8/50
34/34 ━━━━━━━━━━━━━━━━━━━━ 3s 37ms/step - loss: 0.0035 - mae: 0.0466 - val_loss: 0.0189 - val_mae: 0.0611
Epoch 9/50
34/34 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - loss: 0.00

In [ ]:
#LSTM

In [ ]:
import os
import pandas as pd
import numpy as np
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import matplotlib.pyplot as plt
import joblib
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense

# Paths
input_folder = "dataset"
output_models = "output_lstm_models"
output_csv = "output_lstm_csv"
output_graphs = "output_lstm_graphs"
output_logs = "output_lstm_logs"
metrics_file = os.path.join(output_csv, "lstm_metrics.csv")

os.makedirs(output_models, exist_ok=True)
os.makedirs(output_csv, exist_ok=True)
os.makedirs(output_graphs, exist_ok=True)
os.makedirs(output_logs, exist_ok=True)

# Function to create sequences for LSTM
def create_sequences(data, seq_length=5):
    X, y = [], []
    for i in range(len(data) - seq_length):
        X.append(data[i:i+seq_length])
        y.append(data[i+seq_length])
    return np.array(X), np.array(y)

# Metrics storage
metrics_list = []

# Process each CSV file
seq_length = 5
for file in os.listdir(input_folder):
    if file.endswith(".csv"):
        district_name = file.split(".")[0]
        print(f"\n========== Processing: {file} ==========")
        
        # Load CSV with multiple date formats support
        df = pd.read_csv(os.path.join(input_folder, file))
        df['Date'] = pd.to_datetime(df['Date'], infer_datetime_format=True, errors='coerce')
        df = df.dropna(subset=['Date'])
        df = df.sort_values('Date')

        # Fill missing Average Price
        df['Average Price'] = df['Average Price'].fillna(df['Average Price'].mean())

        # Moving averages
        df['MA_7'] = df['Average Price'].rolling(window=7).mean().fillna(df['Average Price'].mean())
        df['MA_30'] = df['Average Price'].rolling(window=30).mean().fillna(df['Average Price'].mean())

        # Scaling
        scaler = MinMaxScaler()
        prices_scaled = scaler.fit_transform(df['Average Price'].values.reshape(-1, 1))

        # Prepare sequences
        X, y = create_sequences(prices_scaled, seq_length)

        # Train-test split (80%-20%)
        split = int(0.8 * len(X))
        X_train, X_test = X[:split], X[split:]
        y_train, y_test = y[:split], y[split:]

        # ✅ Reshape for LSTM: (samples, timesteps, features)
        X_train = X_train.reshape((X_train.shape[0], seq_length, 1))
        X_test = X_test.reshape((X_test.shape[0], seq_length, 1))

        # Build LSTM model
        model = Sequential()
        model.add(LSTM(50, activation='relu', input_shape=(seq_length, 1)))
        model.add(Dense(1))
        model.compile(optimizer='adam', loss='mse', metrics=['mae'])

        # Train model
        history = model.fit(
            X_train, y_train,
            epochs=20,
            batch_size=32,
            validation_data=(X_test, y_test),
            verbose=1
        )

        # Predictions
        y_pred_scaled = model.predict(X_test)
        y_pred = scaler.inverse_transform(y_pred_scaled)
        y_true = scaler.inverse_transform(y_test.reshape(-1, 1))

        # Round Actual & Predicted
        y_true_round = np.round(y_true, 2)
        y_pred_round = np.round(y_pred, 2)

        # Save predictions in CSV
        df_pred = df.iloc[seq_length + split:].copy()
        df_pred['Predicted'] = y_pred_round.flatten()
        df_pred['Average Price'] = y_true_round.flatten()
        df_pred.to_csv(os.path.join(output_csv, f"{district_name}_lstm_updated.csv"), index=False)

        # ✅ Metrics calculation (fixed RMSE)
        mae_val = round(mean_absolute_error(y_true, y_pred), 2)
        rmse_val = round(np.sqrt(mean_squared_error(y_true, y_pred)), 2)  # FIXED
        r2_val = round(r2_score(y_true, y_pred), 2)
        mape_val = round(np.mean(np.abs((y_true - y_pred)/y_true))*100, 2)
        accuracy_val = round(100 - mape_val, 2)

        metrics_list.append([district_name, mae_val, rmse_val, r2_val, mape_val, accuracy_val])
        print(f"✅ Done with {file} | MAE={mae_val}, RMSE={rmse_val}, R2={r2_val}, "
              f"MAPE={mape_val}%, Accuracy={accuracy_val}%")

        # Save model as .pkl
        model_file = os.path.join(output_models, f"{district_name}_lstm_model.pkl")
        joblib.dump(model, model_file)

        # Save prediction graph
        plt.figure(figsize=(12,6))
        plt.plot(df_pred['Date'], df_pred['Average Price'], label='Actual', color='blue')
        plt.plot(df_pred['Date'], df_pred['Predicted'], label='Predicted', color='red', linestyle='dashed')
        plt.xlabel('Date')
        plt.ylabel('Average Price')
        plt.title(f"LSTM Predictions for {district_name}")
        plt.legend()
        plt.grid(True)
        plt.savefig(os.path.join(output_graphs, f"{district_name}_lstm_graph.png"))
        plt.close()

        # Save training loss graph
        plt.figure(figsize=(8,4))
        plt.plot(history.history['loss'], label='Train Loss')
        plt.plot(history.history['val_loss'], label='Val Loss')
        plt.title(f"Training Loss for {district_name}")
        plt.xlabel("Epochs")
        plt.ylabel("Loss")
        plt.legend()
        plt.savefig(os.path.join(output_graphs, f"{district_name}_lstm_training_loss.png"))
        plt.close()

# Save metrics CSV
metrics_df = pd.DataFrame(
    metrics_list,
    columns=['District', 'MAE', 'RMSE', 'R2', 'MAPE(%)', 'Accuracy(%)']
)
metrics_df.to_csv(metrics_file, index=False)

print(f"\n📊 Metrics saved to {metrics_file}")
print("\nAll districts processed successfully!")


========== Processing: wheat_Bagalkot_weekly.csv ==========
Epoch 1/20
18/18 ━━━━━━━━━━━━━━━━━━━━ 8s 68ms/step - loss: 0.0437 - mae: 0.1781 - val_loss: 0.0864 - val_mae: 0.2552
Epoch 2/20
18/18 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - loss: 0.0103 - mae: 0.0732 - val_loss: 0.0139 - val_mae: 0.0733
Epoch 3/20
18/18 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 0.0047 - mae: 0.0559 - val_loss: 0.0140 - val_mae: 0.0800
Epoch 4/20
18/18 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step - loss: 0.0034 - mae: 0.0406 - val_loss: 0.0071 - val_mae: 0.0494
Epoch 5/20
18/18 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step - loss: 0.0022 - mae: 0.0346 - val_loss: 0.0055 - val_mae: 0.0463
Epoch 6/20
18/18 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step - loss: 0.0014 - mae: 0.0246 - val_loss: 0.0050 - val_mae: 0.0443
Epoch 7/20
18/18 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - loss: 0.0010 - mae: 0.0180 - val_loss: 0.0073 - val_mae: 0.0507
Epoch 8/20
18/18 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step - loss: 9.5779e-04 - mae: 0.0164 - val_loss: 0.0075 - val_mae: 0.0520

5/5 ━━━━━━━━━━━━━━━━━━━━ 1s 152ms/step
✅ Done with wheat_Bangalore_weekly.csv | MAE=302.02, RMSE=338.93, R2=0.04, MAPE=9.19%, Accuracy=90.81%

========== Processing: wheat_Belgaum_weekly.csv ==========
Epoch 1/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 6s 50ms/step - loss: 0.0948 - mae: 0.2648 - val_loss: 0.3641 - val_mae: 0.5955
Epoch 2/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - loss: 0.0320 - mae: 0.1432 - val_loss: 0.0944 - val_mae: 0.2995
Epoch 3/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step - loss: 0.0100 - mae: 0.0835 - val_loss: 0.0360 - val_mae: 0.1826
Epoch 4/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - loss: 0.0071 - mae: 0.0713 - val_loss: 0.0271 - val_mae: 0.1590
Epoch 5/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - loss: 0.0045 - mae: 0.0555 - val_loss: 0.0070 - val_mae: 0.0793
Epoch 6/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step - loss: 0.0024 - mae: 0.0389 - val_loss: 0.0019 - val_mae: 0.0324
Epoch 7/20
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - loss: 0.0014 - mae: 0.0281 - val_loss: 0.00

In [ ]:
#GRU

In [ ]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import joblib
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import GRU, Dense, Dropout

# Paths
input_folder = "dataset"
output_models = "gru_output_models"
output_csv = "gru_output_csv"
output_graphs = "gru_output_graphs"
output_logs = "gru_output_logs"
metrics_file = os.path.join(output_csv, "gru_metrics.csv")

os.makedirs(output_models, exist_ok=True)
os.makedirs(output_csv, exist_ok=True)
os.makedirs(output_graphs, exist_ok=True)
os.makedirs(output_logs, exist_ok=True)

# Function to create dataset sequences
def create_dataset(data, look_back=30):
    X, y = [], []
    for i in range(len(data) - look_back):
        X.append(data[i:i+look_back, 0])
        y.append(data[i+look_back, 0])
    return np.array(X), np.array(y)

# Store metrics for all files
metrics_list = []

# Process each CSV file
look_back = 30
for file in os.listdir(input_folder):
    if file.endswith(".csv"):
        district_name = file.split(".")[0]
        print(f"\n========== Processing: {file} ==========")
        
        # Load CSV with multiple date formats support
        df = pd.read_csv(os.path.join(input_folder, file))
        df['Date'] = pd.to_datetime(df['Date'], infer_datetime_format=True, errors='coerce')
        df = df.dropna(subset=['Date'])
        df = df.sort_values('Date')

        # Fill missing Average Price
        df['Average Price'] = df['Average Price'].fillna(df['Average Price'].mean())

        # Moving averages
        df['MA_7'] = df['Average Price'].rolling(window=7).mean().fillna(df['Average Price'].mean())
        df['MA_30'] = df['Average Price'].rolling(window=30).mean().fillna(df['Average Price'].mean())

        # Prepare data
        values = df[['Average Price']].values
        scaler = MinMaxScaler(feature_range=(0, 1))
        scaled_values = scaler.fit_transform(values)

        X, y = create_dataset(scaled_values, look_back)
        X = X.reshape((X.shape[0], X.shape[1], 1))

        # Train-test split (80%-20%)
        split = int(0.8 * len(X))
        X_train, X_test = X[:split], X[split:]
        y_train, y_test = y[:split], y[split:]

        # Build GRU model
        model = Sequential()
        model.add(GRU(64, return_sequences=True, input_shape=(look_back, 1)))
        model.add(Dropout(0.2))
        model.add(GRU(32))
        model.add(Dropout(0.2))
        model.add(Dense(1))
        model.compile(optimizer="adam", loss="mse", metrics=['mae'])

        # Train model
        history = model.fit(
            X_train, y_train,
            epochs=20,
            batch_size=16,
            validation_data=(X_test, y_test),
            verbose=1
        )

        # Save training log
        log_file = os.path.join(output_logs, f"{district_name}_gru_training.txt")
        with open(log_file, "w") as f:
            f.write("Epoch\tTrain_Loss\tVal_Loss\n")
            for i, (loss, val_loss) in enumerate(zip(history.history['loss'], history.history['val_loss'])):
                f.write(f"{i+1}\t{loss:.6f}\t{val_loss:.6f}\n")

        # Predict
        y_pred_scaled = model.predict(X_test)
        y_pred = scaler.inverse_transform(y_pred_scaled)
        y_true = scaler.inverse_transform(y_test.reshape(-1, 1))

        # Round Actual & Predicted
        y_true_round = np.round(y_true, 2)
        y_pred_round = np.round(y_pred, 2)

        # Save predictions in CSV
        df_pred = df.iloc[-len(y_true):].copy()
        df_pred['Predicted'] = y_pred_round.flatten()
        df_pred['Average Price'] = y_true_round.flatten()
        df_pred.to_csv(os.path.join(output_csv, f"{district_name}_gru_updated.csv"), index=False)

        # ✅ Metrics calculation (RMSE fixed)
        mae_val = round(mean_absolute_error(y_true, y_pred), 2)
        rmse_val = round(np.sqrt(mean_squared_error(y_true, y_pred)), 2)  # FIXED
        r2_val = round(r2_score(y_true, y_pred), 2)
        mape_val = round(np.mean(np.abs((y_true - y_pred)/y_true))*100, 2)
        accuracy_val = round(100 - mape_val, 2)
        metrics_list.append([district_name, mae_val, rmse_val, r2_val, mape_val, accuracy_val])

        print(f"✅ Done with {file} | MAE={mae_val}, RMSE={rmse_val}, R2={r2_val}, "
              f"MAPE={mape_val}%, Accuracy={accuracy_val}%")

        # Save model as .pkl
        model_file = os.path.join(output_models, f"{district_name}_gru_model.pkl")
        joblib.dump(model, model_file)

        # Save prediction graph
        plt.figure(figsize=(12,6))
        plt.plot(df_pred['Date'], df_pred['Average Price'], label="Actual", color="blue")
        plt.plot(df_pred['Date'], df_pred['Predicted'], label="Predicted (GRU)", color="red", linestyle="dashed")
        plt.plot(df_pred['Date'], df_pred['MA_7'], label="MA_7", color="orange")
        plt.plot(df_pred['Date'], df_pred['MA_30'], label="MA_30", color="green")
        plt.xlabel("Date")
        plt.ylabel("Average Price")
        plt.title(f"GRU Predictions - {district_name}")
        plt.legend()
        plt.grid(True)
        plt.savefig(os.path.join(output_graphs, f"{district_name}_gru_graph.png"))
        plt.close()

        # Save training loss graph
        plt.figure(figsize=(8,4))
        plt.plot(history.history['loss'], label='Train Loss')
        plt.plot(history.history['val_loss'], label='Val Loss')
        plt.title(f"GRU Training Loss - {district_name}")
        plt.xlabel("Epochs")
        plt.ylabel("Loss")
        plt.legend()
        plt.savefig(os.path.join(output_graphs, f"{district_name}_gru_loss.png"))
        plt.close()

# Save metrics CSV
metrics_df = pd.DataFrame(metrics_list, columns=['District', 'MAE', 'RMSE', 'R2', 'MAPE(%)', 'Accuracy(%)'])
metrics_df.to_csv(metrics_file, index=False)
print("\n📊 Metrics saved to", metrics_file)
print("\n✅ All districts processed successfully!")